In [1]:
import os
import sys
os.environ["PYSPARK_PYTHON"]='/opt/anaconda/envs/bd9/bin/python'
os.environ["SPARK_HOME"]='/usr/hdp/current/spark2-client'
os.environ["PYSPARK_SUBMIT_ARGS"]='--num-executors 5 --executor-memory 4g --executor-cores 1 --driver-memory 3g pyspark-shell'

spark_home = os.environ.get('SPARK_HOME', None)

sys.path.insert(0, os.path.join(spark_home, 'python'))
sys.path.insert(0, os.path.join(spark_home, 'python/lib/py4j-0.10.7-src.zip'))

In [2]:
from pyspark.sql import SparkSession

spark = SparkSession.builder \
                    .master("local[2]") \
                    .appName("ML app") \
                    .config("spark.driver.memory", "512m") \
                    .config("spark.jars.packages", "org.apache.spark:spark-sql-kafka-0-10_2.11:2.4.5") \
                    .getOrCreate()

spark

In [3]:
from pyspark.sql.functions import json_tuple, from_json, get_json_object, col, explode, expr, \
collect_set, collect_list,regexp_replace, get_json_object, to_json, struct
import pyspark.sql.types as t
import pyspark.sql.functions as f

from pyspark.sql.types import StructField, StructType, StringType, ArrayType, IntegerType, TimestampType, LongType
from pyspark.ml.feature import HashingTF, IDF, Tokenizer, StopWordsRemover, StringIndexer, IndexToString
from pyspark.ml import Pipeline, PipelineModel
from pyspark.ml.linalg import Vector, DenseVector
from pyspark.ml.classification import LogisticRegression ,DecisionTreeClassifier, RandomForestClassifier, GBTClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
import json, pprint

In [7]:
! hdfs dfs -ls "/labs/slaba04/"

Found 1 items
-rw-r--r--   3 hdfs hdfs  655090069 2022-01-06 18:46 /labs/slaba04/gender_age_dataset.txt


In [8]:
! hdfs dfs -cat "/labs/slaba04/gender_age_dataset.txt"

gender	age	uid	user_json
F	18-24	d50192e5-c44e-4ae8-ae7a-7cfe67c8b777	{"visits": [{"url": "http://zebra-zoya.ru/200028-chehol-organayzer-dlja-macbook-11-grid-it.html?utm_campaign=397720794&utm_content=397729344&utm_medium=cpc&utm_source=begun", "timestamp": 1419688144068}, {"url": "http://news.yandex.ru/yandsearch?cl4url=chezasite.com/htc/htc-one-m9-delay-86327.html&lr=213&rpt=story", "timestamp": 1426666298001}, {"url": "http://www.sotovik.ru/news/240283-htc-one-m9-zaderzhivaetsja.html", "timestamp": 1426666298000}, {"url": "http://news.yandex.ru/yandsearch?cl4url=chezasite.com/htc/htc-one-m9-delay-86327.html&lr=213&rpt=story", "timestamp": 1426661722001}, {"url": "http://www.sotovik.ru/news/240283-htc-one-m9-zaderzhivaetsja.html", "timestamp": 1426661722000}]}
M	25-34	d502331d-621e-4721-ada2-5d30b2c3801f	{"visits": [{"url": "http://sweetrading.ru/?p=900", "timestamp": 1419717886224}, {"url": "http://sweetrading.ru/?p=884", "timestamp": 1419717884437}, {"url": "http://sweetrading.ru/?

F	45-54	d52fdc8d-9250-41b6-9d00-4a66c52e9408	{"visits": [{"url": "http://1prime.ru/state_regulation/20150316/804971268.html?utm_source=infox.sg", "timestamp": 1427208600001}, {"url": "http://www.infox.sg/others/frame/putin-razveyal-sluhi-o-problemah-so-zdorovem/", "timestamp": 1427208600000}, {"url": "http://www.womanhit.ru/stars/news/660904-irina-i-sergey-bezrukovyi-obratilis-k-smi.html", "timestamp": 1427123416000}, {"url": "http://www.womanhit.ru/stars/news/660904-irina-i-sergey-bezrukovyi-obratilis-k-smi.html", "timestamp": 1427123414001}, {"url": "http://news.smi2.ru/newdata/news?ad=715515&bl=74662&st=14&ct=adpreview&out=1", "timestamp": 1427123414000}, {"url": "http://content.adfox.ru/130905/adfox/230780/845730_1.html", "timestamp": 1427122889000}, {"url": "http://7days.ru/news/dochka-ksenii-borodinoy-stala-modelyu.htm", "timestamp": 1427122809000}, {"url": "http://7days.ru/caravan/2013/7/natasha-koroleva-my-byli-v-shoke-kogda-uznali-matvey-autist/25.htm", "timestamp": 1427121784

M	>=55	d5412b21-d392-454b-9991-cebb388d3ea6	{"visits": [{"url": "http://www.openli.ru/arhiv/11098", "timestamp": 1419718935600}, {"url": "http://vesti.lv/news/melynikova-rossiya-brosila-svoih-soldat-v-ukraine", "timestamp": 1419539021172}, {"url": "http://vesti.lv/news/melynikova-rossiya-brosila-svoih-soldat-v-ukraine?utm_source=delfi&utm_medium=news-widget&utm_campaign=links-in-partner-sites", "timestamp": 1419539002983}, {"url": "http://www.sportsdaily.ru/news/tsska-razgromno-proigral-bavarii-vyiletev-iz-ligi-chempionov-effektnyiy-gol-gettse-i-novaya-drama-akinfeeva-video-203442", "timestamp": 1418265333507}, {"url": "http://podrobnosti.ua/society/2014/12/04/1006001.html", "timestamp": 1417730113342}, {"url": "http://podrobnosti.ua/society/2014/12/04/1006000.html", "timestamp": 1417730027620}, {"url": "http://podrobnosti.ua/society/2014/12/04/1005987.html", "timestamp": 1417729914978}, {"url": "http://online.translate.ua/ru?h=420&w=600&url=translate.ua&maindirect=ukrainian-russian&co

F	45-54	d57684f5-7bf1-4345-8cbe-6fdc93629459	{"visits": [{"url": "http://mogilev.gov.by/", "timestamp": 1427001814000}, {"url": "http://mogilev.gov.by/", "timestamp": 1426828074000}]}
M	18-24	d576d60e-8d3f-4dc3-97a4-3aeb5a097631	{"visits": [{"url": "http://www.the-digital-picture.com/reviews/iso-12233-sample-crops.aspx?lens=824", "timestamp": 1418846565892}, {"url": "http://www.the-digital-picture.com/reviews/iso-12233-sample-crops.aspx?lens=824", "timestamp": 1418846559413}, {"url": "http://www.the-digital-picture.com/reviews/iso-12233-sample-crops.aspx?lens=824", "timestamp": 1418846527715}, {"url": "http://www.the-digital-picture.com/reviews/iso-12233-sample-crops.aspx?lens=824", "timestamp": 1418846505689}, {"url": "http://www.the-digital-picture.com/reviews/iso-12233-sample-crops.aspx?lens=824", "timestamp": 1418846453632}, {"url": "http://www.the-digital-picture.com/reviews/iso-12233-sample-crops.aspx?lens=824", "timestamp": 1418846414674}, {"url": "http://www.the-digital-picture

F	45-54	d5ad6249-1f0b-44fa-84d4-0489a403f63f	{"visits": [{"url": "http://kanzashimk.com/", "timestamp": 1419914829153}, {"url": "http://bebi.lv/kanzashi-mk/kak-ukrsit-zakolki-dlya-volos-tsvetami-kanzashi.html", "timestamp": 1419914759055}, {"url": "http://www.labirint.ru/books/456501/", "timestamp": 1418752388352}, {"url": "http://www.labirint.ru/office/455114/", "timestamp": 1418752225465}, {"url": "http://www.labirint.ru/office/455115/", "timestamp": 1418752224245}, {"url": "http://www.labirint.ru/office/455117/", "timestamp": 1418752220023}, {"url": "http://www.labirint.ru/office/455116/", "timestamp": 1418752193717}, {"url": "http://www.labirint.ru/office/466613/", "timestamp": 1418752064339}, {"url": "http://www.labirint.ru/office/457161/", "timestamp": 1418751851373}, {"url": "http://www.labirint.ru/books/310748/", "timestamp": 1418751677954}, {"url": "http://www.labirint.ru/books/218233/", "timestamp": 1418751623372}, {"url": "http://www.labirint.ru/books/310748/", "timestamp": 

...

F	35-44	43b59f91-5cc6-4c2a-a53a-b7b035e80646	{"visits": [{"url": "http://www.gismeteo.ru/city/weekly/4407/", "timestamp": 1427164915000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom_503663557", "timestamp": 1426864298000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom_505692579", "timestamp": 1426864255000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom_506878513", "timestamp": 1426864250000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom_508905286", "timestamp": 1426864240000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom_509924466", "timestamp": 1426864229000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom_115107682", "timestamp": 1426864115000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom_518956949", "timestamp": 1426864061000}, {"url": "https://www.avito.ru/ulyanovsk/doma_dachi_kottedzhi/kuplyu_dom

M	35-44	43ba0a03-ec02-4abc-bb00-3dc5a5a1a23c	{"visits": [{"url": "http://www.dissercat.com/content/sistema-vzaimootnoshenii-rossiiskogo-kommercheskogo-banka-s-klientami", "timestamp": 1419879447611}, {"url": "http://www.banki-delo.ru/2009/12/\u0437\u0430\u043b\u043e\u0433-\u0438-\u0437\u0430\u043b\u043e\u0433\u043e\u0432\u044b\u0439-\u043c\u0435\u0445\u0430\u043d\u0438\u0437\u043c/", "timestamp": 1419791994800}, {"url": "http://www.bankmib.ru/1078", "timestamp": 1419786140149}, {"url": "http://www.bankmib.ru/1078", "timestamp": 1419786139891}, {"url": "http://www.xvideos.com/video3980882/my_sister_wants_to_be_a_stripper_at_hornbunny_-_watch_free_porn_videos", "timestamp": 1419785091011}, {"url": "http://www.xvideos.com/profiles/lila35", "timestamp": 1419784226490}, {"url": "http://www.xvideos.com/profiles/lila35", "timestamp": 1419784218339}, {"url": "http://www.xvideos.com/profiles/rulora", "timestamp": 1419784214899}, {"url": "http://www.xvideos.com/profiles/malloy1987", "timestamp":

nt=ad-5476898", "timestamp": 1418714678341}, {"url": "http://chessok.net/chessonline/", "timestamp": 1418707731753}, {"url": "http://www.xvideos.com/video7161635/naughty_brunette_anita_berlusconi_fingers_and_fists_her_ass", "timestamp": 1418638405172}, {"url": "http://udf.by/news/economic/114645-evro-vpervye-prevysil-73-rublya.html", "timestamp": 1418636519375}, {"url": "http://www.xvideos.com/video4597767/slutty_fucking_russian_milf", "timestamp": 1418546492670}, {"url": "http://www.xvideos.com/video5147086/horny_mature_aunt_with_glasses_gives_her_nephew_one_hell_of_a_fucking_blowjob", "timestamp": 1418546415503}, {"url": "http://www.xvideos.com/video6627013/son_helps_mom_to_get_rid_of_problems", "timestamp": 1418546360891}, {"url": "http://www.xvideos.com/video7660643/this_might_upset_your_father_son", "timestamp": 1418546232384}, {"url": "http://www.xvideos.com/video2542174/he_have_fucked_the_mother_of_his_girlfriend", "timestamp": 1418546230109}, {"url": "http://www.xvideos.com/vid

M	18-24	43be2586-2bf5-4e22-9b41-7228d4221953	{"visits": [{"url": "http://www.nudevista.tv/?q=\u043c\u043d\u043e\u0436\u0435\u0441\u0442\u0432\u0435\u043d\u043d\u044b\u0439&s=t", "timestamp": 1418637629864}, {"url": "http://www.productynadom.ru/ribeye-steak-argentyna.html", "timestamp": 1418558205746}, {"url": "http://lostfilmonline.tv/movie/3892", "timestamp": 1418320345567}, {"url": "http://lostfilmonline.tv/series/119", "timestamp": 1418320340015}, {"url": "http://rubeeg.ru/videos/10829/seksualnaya-bryunetka-s-nebritym-lobkom-daet-v-pizdu-borodachu/", "timestamp": 1418217125851}, {"url": "http://rubeeg.ru/seks-porno-video/rejtingovye-seks-porno-video-roliki/", "timestamp": 1418217098114}, {"url": "http://rubeeg.ru/videos/10141/vyazannaya-grechanka-imeet-seks-stoya-posle-nejnogo-kunilingusa/", "timestamp": 1418217083294}, {"url": "http://spartak.msk.ru/guest/viewtopic.php?f=35&t=2074", "timestamp": 1418149704587}, {"url": "http://www.nudevista.tv/?q=\u0441\u0438\u043b\u044c\u043d\u043

M	18-24	43c4d967-9358-4eb3-a9eb-603ab49a7f4f	{"visits": [{"url": "http://staroetv.su/video/vip/7871/ct_sssr/utrennjaja_pochta_ct_1986_vesjolye_rebjata_galina_zhadushkina_larisa_golubkina_i_aleksandr_shirvindt_irina_ponarovskaja", "timestamp": 1419801578914}, {"url": "http://staroetv.su/video/vip/8137/reklama/reklama_avtobiograficheskoj_povesti_v_v_zhirinovskogo_tv_6_ijun_1996", "timestamp": 1419796448462}, {"url": "http://staroetv.su/video/vip/8141/rtr_rossija_1/anshlag_rtr_dekabr_2000_okonchanie_vypuska", "timestamp": 1419793997359}, {"url": "http://staroetv.su/video/vip/8140/reklama/reklama_tv_6_mart_1998_delmy_levante_alldays_snickers_fairy_cvety_rossii", "timestamp": 1419790083502}, {"url": "http://staroetv.su/video/vip/8138/reklama/reklama_pjatyj_kanal_1996_ultra_diem_trit_voimix_ehra_clairol_whirlpool", "timestamp": 1419789767034}, {"url": "http://staroetv.su/news/2014-12-24-3392", "timestamp": 1419788792899}, {"url": "http://staroetv.su/news/2014-12-28-3396", "timestamp": 141978

In [50]:
#df = spark.read.csv("/labs/slaba04/gender_age_dataset.txt", header=True, inferSchema=True, sep='\t')
#df.show(1, truncate=False, vertical=True)
#print(df)

In [5]:
path = "/labs/slaba04/gender_age_dataset.txt"

schema = StructType(fields=[
    t.StructField('gender', StringType()),
    t.StructField('age', StringType()),
    t.StructField('uid', StringType()),
    t.StructField('user_json', StringType()),
])

df = spark.read.csv(path, header=True, schema=schema, sep='\t')
df.show(1, truncate=False, vertical=True)
print(df)

-RECORD 0-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
 gender    | F                                                                                                                                                                                                                                                                             

In [4]:
VisitsType = StructType([
    StructField("visits", ArrayType(
        StructType([
            StructField("url", StringType(), True),
            StructField("timestamp", LongType(), True) 
            ])
        ))
    ])

In [7]:
df_flattened = df \
    .withColumn("visits", from_json(col("user_json"), VisitsType)) \
    .withColumn("visit", explode("visits.visits").alias("visit")) \
    .withColumn("host", expr("parse_url(visit.url, 'HOST')").alias("host")) \
    .drop("visits", "visit","user_json")
df_flattened.show(2, truncate=False, vertical=True)

-RECORD 0--------------------------------------
 gender | F                                    
 age    | 18-24                                
 uid    | d50192e5-c44e-4ae8-ae7a-7cfe67c8b777 
 host   | zebra-zoya.ru                        
-RECORD 1--------------------------------------
 gender | F                                    
 age    | 18-24                                
 uid    | d50192e5-c44e-4ae8-ae7a-7cfe67c8b777 
 host   | news.yandex.ru                       
only showing top 2 rows



In [69]:
df_flattened.where(col("host").isNull()).show(2, truncate=False, vertical=True)

-RECORD 0--------------------------------------
 gender | M                                    
 age    | 25-34                                
 uid    | d502331d-621e-4721-ada2-5d30b2c3801f 
 host   | null                                 
-RECORD 1--------------------------------------
 gender | M                                    
 age    | >=55                                 
 uid    | d503c3b2-a0c2-4f47-bb27-065058c73008 
 host   | null                                 
only showing top 2 rows



In [8]:
df_final = df_flattened \
    .groupBy("gender", "age", "uid") \
    .agg(collect_list("host") \
    .alias("hosts"))\
    .where(col("age") != "-")\
    .where(col("gender") != "-")\
    .filter(f.size('hosts') != 0)
df_final.show(2, truncate=False, vertical=True)

-RECORD 0-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
 gender | F                                                                                                                                                                                                                                                                                             
 age    | 18-24                                                                                                                                                                                                                                                                                         
 uid    | 09b1ecd3-b2d2-4c1b-857a-025c0509d9ec                                                               

In [9]:
X_train, X_test = df_final.randomSplit([0.8, 0.2], seed=777)

In [11]:
hashing_TF = HashingTF(inputCol="hosts", outputCol="rawFeatures", numFeatures=100000, binary=False)
indexer_age = StringIndexer(inputCol="age", outputCol="ageIndex").fit(df_final)
indexer_gender = StringIndexer(inputCol="gender", outputCol="genderIndex").fit(df_final)

In [12]:
rf_age = RandomForestClassifier(featuresCol = 'rawFeatures', labelCol = 'ageIndex', 
                           predictionCol="age_index_prediction", rawPredictionCol="age_index_raw_prediction",
                           probabilityCol = "age_probability")

In [13]:
rf_gender = RandomForestClassifier(featuresCol = 'rawFeatures', labelCol = 'genderIndex',
                              predictionCol="gender_index_prediction", rawPredictionCol="gender_index_raw_prediction",
                              probabilityCol = "gender_probability")

In [14]:
converter_age = IndexToString(inputCol="age_index_prediction", outputCol="PredictedAge", labels=indexer_age.labels)

In [15]:
converter_gender = IndexToString(inputCol="gender_index_prediction", outputCol="PredictedGender", labels=indexer_gender.labels)

In [16]:
pipeline = Pipeline(stages=[hashing_TF, indexer_age, indexer_gender, rf_age, rf_gender, 
                            converter_age, converter_gender])

In [94]:
df_final.count()

35960

In [93]:
df_final.rdd.getNumPartitions()

200

In [96]:
df_final.repartition(15).rdd.getNumPartitions()

15

In [17]:
X_train, X_test = df_final.randomSplit([0.8, 0.2], seed=777)
X_train.repartition(15)
X_train.cache()

DataFrame[gender: string, age: string, uid: string, hosts: array<string>]

In [18]:
model = pipeline.fit(X_train)

In [19]:
predictions = model.transform(X_test)

In [20]:
evaluator_age = MulticlassClassificationEvaluator(
    labelCol="ageIndex", predictionCol="age_index_prediction", metricName="accuracy")
accuracy_age = evaluator_age.evaluate(predictions)
evaluator_gender = MulticlassClassificationEvaluator(
    labelCol="genderIndex", predictionCol="gender_index_prediction", metricName="accuracy")
accuracy_gender = evaluator_gender.evaluate(predictions)

print("Accuracy for age: " + str(accuracy_age))
print("Accuracy for gender: " + str(accuracy_gender))

Accuracy for age: 0.42790958865646495
Accuracy for gender: 0.5451354766250176


In [21]:
model.write().overwrite().save("/user/stanislav.mosin/lab04_model")

In [23]:
KAFKA_BOOTSTRAP_SERVER = 'spark-node-1.newprolab.com:6667'
KAFKA_INPUT_TOPIC = 'input_stanislav.mosin'
KAFKA_OUTPUT_TOPIC = 'stanislav.mosin'

In [24]:
# чтение в статическом режиме

kafka_read_df = (
    spark.read
    .format('kafka')
    .option('kafka.bootstrap.servers', KAFKA_BOOTSTRAP_SERVER)
    .option('subscribe', KAFKA_INPUT_TOPIC)
    .option('startingOffsets', 'earliest')
    .option('failOnDataLoss', 'False')
    .load()
    .cache()
)

In [36]:
kafka_read_df.show(3)

+----+--------------------+--------------------+---------+------+--------------------+-------------+
| key|               value|               topic|partition|offset|           timestamp|timestampType|
+----+--------------------+--------------------+---------+------+--------------------+-------------+
|null|[7B 22 75 69 64 2...|input_stanislav.m...|        0|     0|2022-11-05 11:46:...|            0|
|null|[7B 22 75 69 64 2...|input_stanislav.m...|        0|     1|2022-11-05 11:46:...|            0|
|null|[7B 22 75 69 64 2...|input_stanislav.m...|        0|     2|2022-11-05 11:46:...|            0|
+----+--------------------+--------------------+---------+------+--------------------+-------------+
only showing top 3 rows



In [25]:
# Парсинг бинарного файла из кафки

event_schema = t.StructType([
    t.StructField('uid', t.StringType(), True),
    t.StructField('visits', t.StringType(), True),
])


visit_schema = t.ArrayType(
    t.StructType([
        t.StructField('url', t.StringType(), True),
        t.StructField('timestamp', t.LongType(), True)
    ])
)


clean_df = (
    kafka_read_df
    .select(f.col('value').cast('string').alias('value'))
    .select(f.from_json(f.col('value'), event_schema).alias('event'))
    .select(
        'event.uid', 
        f.from_json(f.col('event.visits'), visit_schema).alias('visits')
    )
)



clean_df.show(3)

+--------------------+--------------------+
|                 uid|              visits|
+--------------------+--------------------+
|bd7a30e1-a25d-4cb...|[[http://www.inte...|
|bd7a6f52-45db-49b...|[[https://www.pac...|
|bd7a7fd9-ab06-42f...|[[http://www.mk.r...|
+--------------------+--------------------+
only showing top 3 rows



In [ ]:
clean_df.show(3)

In [26]:
inf_model = PipelineModel.load("/user/stanislav.mosin/lab04_model")

In [27]:
prep_df = clean_df \
    .withColumn("visit", explode("visits").alias("visit")) \
    .withColumn("host", expr("parse_url(visit.url, 'HOST')").alias("host")) \
    .drop("visits", "visit") \
    .groupBy("uid") \
    .agg(collect_list("host").alias("hosts"))

predictions_df = inf_model.transform(prep_df) \
    .select("uid", "PredictedGender", "PredictedAge") \
    .withColumnRenamed("PredictedAge","age") \
    .withColumnRenamed("PredictedGender","gender")

In [34]:
prep_df.show(3)

+--------------------+--------------------+
|                 uid|               hosts|
+--------------------+--------------------+
|0108d217-e476-493...|[kvartblog.ru, kv...|
|0192cc54-559c-4c8...|[metanol.lv, meta...|
|019acd5e-be9a-4cd...|[www.russianfood....|
+--------------------+--------------------+
only showing top 3 rows



In [35]:
predictions_df.show(3)

+--------------------+------+-----+
|                 uid|gender|  age|
+--------------------+------+-----+
|0108d217-e476-493...|     M|25-34|
|0192cc54-559c-4c8...|     M|25-34|
|019acd5e-be9a-4cd...|     M|25-34|
+--------------------+------+-----+
only showing top 3 rows



In [52]:
# извлечение url

# применение модели, сохранение предсказаний в predictions_df  

# Оборачивание предсказания обратно в json

kafka_out_df = (
    predictions_df.select(f.to_json(f.struct(*predictions_df.columns)).alias('value'))
)

# Запись в выходной топикa

(
    kafka_out_df
    .write
    .format('kafka')
    .option('kafka.bootstrap.servers', KAFKA_BOOTSTRAP_SERVER)
    .option('topic', KAFKA_OUTPUT_TOPIC)
    .save()
)

In [38]:
kafka_out_df.show(2, truncate=False, vertical=True)

-RECORD 0--------------------------------------------------------------------------
 value | {"uid":"0108d217-e476-493d-8c81-a9744f12451a","gender":"M","age":"25-34"} 
-RECORD 1--------------------------------------------------------------------------
 value | {"uid":"0192cc54-559c-4c8e-89b4-5f4bf31e4245","gender":"M","age":"25-34"} 
only showing top 2 rows



In [53]:
kafka_out_df.count()

5000

In [54]:
kafka_stream = (
    spark
    .readStream
    .format('kafka')
    .option('kafka.bootstrap.servers', KAFKA_BOOTSTRAP_SERVER)
    .option('subscribe', KAFKA_INPUT_TOPIC)
    .option('startingOffsets', 'earliest')
    .option('failOnDataLoss', 'False')
    .load()
)

In [55]:
# предсказание и запись

kafka_write_stream = (
    predictions_df
    .select(f.to_json(f.struct(*predictions_df.columns)).alias('value'))
    .write
    .format("kafka")
#    .outputMode("append")
    .option("checkpointLocation", "checkpoints/checkpoints_lab04")
    .option("kafka.bootstrap.servers", KAFKA_BOOTSTRAP_SERVER)
    .option("topic", KAFKA_OUTPUT_TOPIC)
)
#kafka_write_stream.start()

In [56]:
! hdfs dfs -ls "/user/stanislav.mosin"

Found 2 items
drwxr-xr-x   - stanislav.mosin stanislav.mosin          0 2022-11-05 03:00 /user/stanislav.mosin/.sparkStaging
drwxr-xr-x   - stanislav.mosin stanislav.mosin          0 2022-11-05 15:42 /user/stanislav.mosin/lab04_model


In [49]:
kafka_write_stream.save("/user/stanislav.mosin/test")